# Training the Super-Resolution CNN

In this tutorial we will train a single image super-resolution CNN using a mean squared error cost function.

In [1]:
from __future__ import print_function, division
import scipy
from keras.optimizers import Adam
import datetime
import matplotlib.pyplot as plt
import numpy as np
import os
import keras.backend as K
import glob
from skimage.transform import resize
from random import shuffle
import sys
MY_UTILS_PATH = "../Modules/"
if not MY_UTILS_PATH in sys.path:
    sys.path.append(MY_UTILS_PATH)
import cnn_utils

/home/roberto/Documents/virtualenv/venv04/local/lib/python2.7/site-packages/h5py/__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters
Using TensorFlow backend.


In [3]:
optimizer = Adam(0.0002, 0.5)
model = cnn_utils.sr_cnn(patch_size = (128,128))
model.compile(loss='mean_squared_error', optimizer=optimizer)
print(model.summary())

__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_1 (InputLayer)            (None, 128, 128, 1)  0                                            
__________________________________________________________________________________________________
conv2d_1 (Conv2D)               (None, 128, 128, 64) 5248        input_1[0][0]                    
__________________________________________________________________________________________________
activation_1 (Activation)       (None, 128, 128, 64) 0           conv2d_1[0][0]                   
__________________________________________________________________________________________________
conv2d_2 (Conv2D)               (None, 128, 128, 64) 36928       activation_1[0][0]               
__________________________________________________________________________________________________
activation

In [4]:
def imread(path):
    return scipy.misc.imread(path, mode = "L").astype(np.float)

def load_data(data_list,img_res=(128, 128), batch_size = 1):
    batch_images = np.random.choice(data_list, size=batch_size)
    imgs_hr = []
    imgs_lr = []
    for img_path in batch_images:
        img = imread(img_path)
        img_lr = resize(img, img_res,anti_aliasing = True)
        # If training => do random flip
        if np.random.random() < 0.5:
            img = np.fliplr(img)
            img_lr = np.fliplr(img_lr)

        imgs_hr.append(img[:,:,np.newaxis])
        imgs_lr.append(img_lr[:,:,np.newaxis])
    imgs_hr = np.array(imgs_hr) / 127.5 - 1.
    imgs_lr = np.array(imgs_lr) / 127.5 - 1.
    return imgs_hr, imgs_lr

In [5]:
def save_imgs(epoch,model):
    #os.makedirs('images/%s' % self.dataset_name, exist_ok=True)
    r, c = 2, 2

    imgs_hr, imgs_lr = load_data(val,img_res=(128, 128), batch_size = 2)
    fake_hr = model.predict(imgs_lr)

    # Rescale images 0 - 1
    imgs_lr = 0.5 * imgs_lr + 0.5
    fake_hr = 0.5 * fake_hr + 0.5
    imgs_hr = 0.5 * imgs_hr + 0.5

    # Save generated images and the high resolution originals
    titles = ['Generated', 'Original']
    fig, axs = plt.subplots(r, c)
    for row in range(r):
        for col, image in enumerate([fake_hr, imgs_hr]):
            axs[row, col].imshow(image[row,:,:,0],cmap = 'gray')
            axs[row, col].set_title(titles[col])
            axs[row, col].axis('off')
    fig.savefig("../Data/cnn_sr_images/%d.png" % (epoch))
    plt.close()

    # Save low resolution images for comparison
    for i in range(r):
        fig = plt.figure()
        plt.imshow(imgs_lr[i,:,:,0],cmap = 'gray')
        fig.savefig('../Data/cnn_sr_images/%d_lowres%d.png' % (epoch, i))
        plt.close()
    return 

In [6]:
loss = 1e+20
epochs = 50000
batch_size = 4
save_interval = 100
path = glob.glob('../Data/carotid_slices/*.png')
shuffle(path)
n = int(0.3*len(path))
train = path[:-n]
val = path[-n:]
start_time = datetime.datetime.now()
for epoch in xrange(epochs):
    # Sample images and their conditioning counterparts
    imgs_hr, imgs_lr = load_data(train,img_res=(128, 128), batch_size = batch_size)
    model.train_on_batch(imgs_lr,imgs_hr)
    imgs_hr, imgs_lr = load_data(val,img_res=(128, 128), batch_size = batch_size)
    new_loss = model.evaluate(imgs_lr,imgs_hr)
    if new_loss < loss:
        loss = new_loss
        model.save_weights("sr_cnn.hdf5")
    elapsed_time = datetime.datetime.now() - start_time
    # Plot the progress
    print ("%d time: %s" % (epoch, elapsed_time))
    print ("Loss: %f" %loss)
    # If at save interval => save generated image samples
    if epoch % save_interval == 0:
        save_imgs(epoch,model)

/home/roberto/Documents/virtualenv/venv04/lib/python2.7/site-packages/ipykernel_launcher.py:2: DeprecationWarning: `imread` is deprecated!
`imread` is deprecated in SciPy 1.0.0, and will be removed in 1.2.0.
Use ``imageio.imread`` instead.
  
/home/roberto/Documents/virtualenv/venv04/local/lib/python2.7/site-packages/scikit_image-0.14.dev0-py2.7-linux-x86_64.egg/skimage/transform/_warps.py:105: UserWarning: The default mode, 'constant', will be changed to 'reflect' in skimage 0.15.
  warn("The default mode, 'constant', will be changed to 'reflect' in "


4/4 [==============================] - 1s 134ms/step
0 time: 0:00:13.308516
Loss: 0.128836
4/4 [==============================] - 0s 40ms/step
1 time: 0:00:14.907488
Loss: 0.128836
4/4 [==============================] - 0s 39ms/step
2 time: 0:00:15.764240
Loss: 0.123244
4/4 [==============================] - 0s 39ms/step
3 time: 0:00:16.612188
Loss: 0.061885
4/4 [==============================] - 0s 39ms/step
4 time: 0:00:17.282339
Loss: 0.061885
4/4 [==============================] - 0s 40ms/step
5 time: 0:00:18.036604
Loss: 0.061885
4/4 [==============================] - 0s 40ms/step
6 time: 0:00:18.921930
Loss: 0.055697
4/4 [==============================] - 0s 40ms/step
7 time: 0:00:19.656043
Loss: 0.055697
4/4 [==============================] - 0s 39ms/step
8 time: 0:00:20.503011
Loss: 0.040345
4/4 [==============================] - 0s 39ms/step
9 time: 0:00:21.233560
Loss: 0.040345
4/4 [==============================] - 0s 39ms/step
10 time: 0:00:22.075251
Loss: 0.030082
4/4 [===

90 time: 0:01:21.094732
Loss: 0.004762
4/4 [==============================] - 0s 40ms/step
91 time: 0:01:21.785378
Loss: 0.004762
4/4 [==============================] - 0s 40ms/step
92 time: 0:01:22.486759
Loss: 0.004762
4/4 [==============================] - 0s 40ms/step
93 time: 0:01:23.188756
Loss: 0.004762
4/4 [==============================] - 0s 40ms/step
94 time: 0:01:24.008958
Loss: 0.004230
4/4 [==============================] - 0s 40ms/step
95 time: 0:01:24.705260
Loss: 0.004230
4/4 [==============================] - 0s 40ms/step
96 time: 0:01:25.410675
Loss: 0.004230
4/4 [==============================] - 0s 40ms/step
97 time: 0:01:26.097273
Loss: 0.004230
4/4 [==============================] - 0s 40ms/step
98 time: 0:01:26.797671
Loss: 0.004230
4/4 [==============================] - 0s 40ms/step
99 time: 0:01:27.517631
Loss: 0.004230
4/4 [==============================] - 0s 40ms/step
100 time: 0:01:28.246724
Loss: 0.004230
4/4 [==============================] - 0s 40ms/ste

4/4 [==============================] - 0s 41ms/step
180 time: 0:02:28.012031
Loss: 0.002649
4/4 [==============================] - 0s 40ms/step
181 time: 0:02:28.713222
Loss: 0.002649
4/4 [==============================] - 0s 40ms/step
182 time: 0:02:29.452149
Loss: 0.002649
4/4 [==============================] - 0s 40ms/step
183 time: 0:02:30.138307
Loss: 0.002649
4/4 [==============================] - 0s 40ms/step
184 time: 0:02:30.891201
Loss: 0.002649
4/4 [==============================] - 0s 40ms/step
185 time: 0:02:31.767867
Loss: 0.002500
4/4 [==============================] - 0s 40ms/step
186 time: 0:02:32.478409
Loss: 0.002500
4/4 [==============================] - 0s 40ms/step
187 time: 0:02:33.202311
Loss: 0.002500
4/4 [==============================] - 0s 41ms/step
188 time: 0:02:33.918797
Loss: 0.002500
4/4 [==============================] - 0s 41ms/step
189 time: 0:02:34.581777
Loss: 0.002500
4/4 [==============================] - 0s 40ms/step
190 time: 0:02:35.318473
Los

269 time: 0:03:33.522640
Loss: 0.002129
4/4 [==============================] - 0s 41ms/step
270 time: 0:03:34.196944
Loss: 0.002129
4/4 [==============================] - 0s 40ms/step
271 time: 0:03:34.891293
Loss: 0.002129
4/4 [==============================] - 0s 40ms/step
272 time: 0:03:35.600354
Loss: 0.002129
4/4 [==============================] - 0s 40ms/step
273 time: 0:03:36.314714
Loss: 0.002129
4/4 [==============================] - 0s 40ms/step
274 time: 0:03:37.011834
Loss: 0.002129
4/4 [==============================] - 0s 41ms/step
275 time: 0:03:37.726754
Loss: 0.002129
4/4 [==============================] - 0s 40ms/step
276 time: 0:03:38.452009
Loss: 0.002129
4/4 [==============================] - 0s 41ms/step
277 time: 0:03:39.155952
Loss: 0.002129
4/4 [==============================] - 0s 41ms/step
278 time: 0:03:39.882091
Loss: 0.002129
4/4 [==============================] - 0s 41ms/step
279 time: 0:03:40.611922
Loss: 0.002129
4/4 [==============================] - 0

...

49576 time: 11:25:45.034048
Loss: 0.000154
4/4 [==============================] - 0s 54ms/step
49577 time: 11:25:45.859782
Loss: 0.000154
4/4 [==============================] - 0s 52ms/step
49578 time: 11:25:46.721221
Loss: 0.000154
4/4 [==============================] - 0s 51ms/step
49579 time: 11:25:47.544506
Loss: 0.000154
4/4 [==============================] - 0s 53ms/step
49580 time: 11:25:48.373769
Loss: 0.000154
4/4 [==============================] - 0s 54ms/step
49581 time: 11:25:49.217929
Loss: 0.000154
4/4 [==============================] - 0s 54ms/step
49582 time: 11:25:50.041901
Loss: 0.000154
4/4 [==============================] - 0s 52ms/step
49583 time: 11:25:50.853107
Loss: 0.000154
4/4 [==============================] - 0s 53ms/step
49584 time: 11:25:51.673049
Loss: 0.000154
4/4 [==============================] - 0s 55ms/step
49585 time: 11:25:52.494771
Loss: 0.000154
4/4 [==============================] - 0s 52ms/step
49586 time: 11:25:53.302637
Loss: 0.000154
4/4 [==

4/4 [==============================] - 0s 54ms/step
49663 time: 11:26:57.387367
Loss: 0.000154
4/4 [==============================] - 0s 49ms/step
49664 time: 11:26:58.179611
Loss: 0.000154
4/4 [==============================] - 0s 54ms/step
49665 time: 11:26:58.999926
Loss: 0.000154
4/4 [==============================] - 0s 52ms/step
49666 time: 11:26:59.811776
Loss: 0.000154
4/4 [==============================] - 0s 54ms/step
49667 time: 11:27:00.632574
Loss: 0.000154
4/4 [==============================] - 0s 49ms/step
49668 time: 11:27:01.444421
Loss: 0.000154
4/4 [==============================] - 0s 49ms/step
49669 time: 11:27:02.305664
Loss: 0.000154
4/4 [==============================] - 0s 52ms/step
49670 time: 11:27:03.156230
Loss: 0.000154
4/4 [==============================] - 0s 49ms/step
49671 time: 11:27:03.995340
Loss: 0.000154
4/4 [==============================] - 0s 52ms/step
49672 time: 11:27:04.847213
Loss: 0.000154
4/4 [==============================] - 0s 52ms/ste

49749 time: 11:28:08.420510
Loss: 0.000154
4/4 [==============================] - 0s 53ms/step
49750 time: 11:28:09.245023
Loss: 0.000154
4/4 [==============================] - 0s 51ms/step
49751 time: 11:28:10.074061
Loss: 0.000154
4/4 [==============================] - 0s 51ms/step
49752 time: 11:28:10.900179
Loss: 0.000154
4/4 [==============================] - 0s 52ms/step
49753 time: 11:28:11.727137
Loss: 0.000154
4/4 [==============================] - 0s 52ms/step
49754 time: 11:28:12.552850
Loss: 0.000154
4/4 [==============================] - 0s 54ms/step
49755 time: 11:28:13.389652
Loss: 0.000154
4/4 [==============================] - 0s 50ms/step
49756 time: 11:28:14.200024
Loss: 0.000154
4/4 [==============================] - 0s 57ms/step
49757 time: 11:28:15.052984
Loss: 0.000154
4/4 [==============================] - 0s 54ms/step
49758 time: 11:28:15.886885
Loss: 0.000154
4/4 [==============================] - 0s 54ms/step
49759 time: 11:28:16.712166
Loss: 0.000154
4/4 [==

4/4 [==============================] - 0s 56ms/step
49836 time: 11:29:19.034290
Loss: 0.000154
4/4 [==============================] - 0s 52ms/step
49837 time: 11:29:19.825288
Loss: 0.000154
4/4 [==============================] - 0s 54ms/step
49838 time: 11:29:20.620699
Loss: 0.000154
4/4 [==============================] - 0s 53ms/step
49839 time: 11:29:21.421734
Loss: 0.000154
4/4 [==============================] - 0s 48ms/step
49840 time: 11:29:22.213962
Loss: 0.000154
4/4 [==============================] - 0s 50ms/step
49841 time: 11:29:23.004026
Loss: 0.000154
4/4 [==============================] - 0s 52ms/step
49842 time: 11:29:23.811788
Loss: 0.000154
4/4 [==============================] - 0s 53ms/step
49843 time: 11:29:24.622497
Loss: 0.000154
4/4 [==============================] - 0s 53ms/step
49844 time: 11:29:25.423560
Loss: 0.000154
4/4 [==============================] - 0s 52ms/step
49845 time: 11:29:26.228584
Loss: 0.000154
4/4 [==============================] - 0s 52ms/ste

49922 time: 11:30:29.568375
Loss: 0.000154
4/4 [==============================] - 0s 47ms/step
49923 time: 11:30:30.322222
Loss: 0.000154
4/4 [==============================] - 0s 46ms/step
49924 time: 11:30:31.078403
Loss: 0.000154
4/4 [==============================] - 0s 47ms/step
49925 time: 11:30:31.836990
Loss: 0.000154
4/4 [==============================] - 0s 47ms/step
49926 time: 11:30:32.594375
Loss: 0.000154
4/4 [==============================] - 0s 46ms/step
49927 time: 11:30:33.361435
Loss: 0.000154
4/4 [==============================] - 0s 45ms/step
49928 time: 11:30:34.099225
Loss: 0.000154
4/4 [==============================] - 0s 46ms/step
49929 time: 11:30:34.843500
Loss: 0.000154
4/4 [==============================] - 0s 47ms/step
49930 time: 11:30:35.591194
Loss: 0.000154
4/4 [==============================] - 0s 46ms/step
49931 time: 11:30:36.326960
Loss: 0.000154
4/4 [==============================] - 0s 47ms/step
49932 time: 11:30:37.108940
Loss: 0.000154
4/4 [==